# Amanzon SageMaker Ground Truth Demonstration for Text Classification

1. [Introduction](#introduction)
2. [Run a Ground Truth labeling job](#run-a-ground-truth-labeling-job)
    1. [Prepare the data](#prepare-the-data)
    2. [Specify the categories](#specify-the-categories)
    3. [Create the instruction template](#create-the-instruction-template)
    4. [Assign private team to test your task](#assign-private-team-to-test-your-task)
    5. [Define pre-built lambda functions for use in the labeling job](#define-pre-built-lambda-functions-for-use-in-the-labeling-job)
    6. [Submit the Ground Truth job request](#submit-the-ground-truth-job-request)
    7. [Monitor job progress](#monitor-job-progress)
    8. [View Task Results](#view-task-results)
3. [Clean Up](#Clean-Up)

## Introduction


This sample notebook takes you through an end-to-end workflow to demonstrate the functionality of SageMaker Ground Truth. We'll start with an unlabeled review text data set, acquire labels for the sentiment like Positive, or Negative  using SageMaker Ground Truth, and analyze the results of the labeling job. Before you begin, we highly recommend you start a Ground Truth labeling job through the AWS Console first to familiarize yourself with the workflow. The AWS Console offers less flexibility than the API, but is simple to use.

#### Cost and runtime
You can run this demo in two modes:
1. Set `RUN_FULL_AL_DEMO = True` in the next cell to label 10k reviews(text). This should cost about \$800 given current [Ground Truth pricing scheme](https://aws.amazon.com/sagemaker/groundtruth/pricing/). In order to reduce the cost, we will use Ground Truth's auto-labeling feature. Auto-labeling uses text classification to learn from human responses and automatically create labels for the easiest review text at a cheap price. The total end-to-end runtime should be about 20h.
1. Set `RUN_FULL_AL_DEMO = False` in the next cell to label only 10 reviews. This should cost about \$.80. **Since Ground Truth's auto-labeling feature only kicks in for datasets of 1000 images or more, this cheaper version of the demo will not use it. Some of the analysis plots might look awkward, but you should still be able to see good results on the human-annotated 100 images.**

#### Prerequisites
To run this notebook, you can simply execute each cell one-by-one. To understand what's happening, you'll need:
* An S3 bucket you can write to -- please provide its name in the following cell. The bucket must be in the same region as this SageMaker Notebook instance. You can also change the `EXP_NAME` to any valid S3 prefix. All the files related to this experiment will be stored in that prefix of your bucket.
* Familiarity with Python and [numpy](http://www.numpy.org/).
* Basic familiarity with [AWS S3](https://docs.aws.amazon.com/s3/index.html),
* Basic understanding of [AWS Sagemaker](https://aws.amazon.com/sagemaker/),
* Basic familiarity with [AWS Command Line Interface (CLI)](https://aws.amazon.com/cli/) -- set it up with credentials to access the AWS account you're running this notebook from. This should work out-of-the-box on SageMaker Jupyter Notebook instances.

This notebook is only tested on a SageMaker notebook instance. The runtimes given are approximate, we used an `ml.m4.xlarge` instance in our tests. However, you can likely run it on a local instance by first executing the cell below on SageMaker, and then copying the `role` string to your local copy of the notebook.

NOTE: This notebook will create/remove subdirectories in its working directory. We recommend to place this notebook in its own directory before running it.

In [4]:
# cell 01
%matplotlib inline
%load_ext autoreload
%autoreload 2
import os
from collections import namedtuple
from collections import defaultdict
from collections import Counter
import itertools
import json
import time
import numpy as np
import pandas as pd
import matplotlib
import matplotlib.pyplot as plt
from matplotlib.backends.backend_pdf import PdfPages
from sklearn.metrics import confusion_matrix
import boto3
import sagemaker
from urllib.parse import urlparse
import warnings
warnings.filterwarnings("ignore", category=DeprecationWarning)

sess = sagemaker.Session()
BUCKET = sess.default_bucket()

EXP_NAME = "label-text/text-classification"  # Any valid S3 prefix.
RUN_FULL_AL_DEMO = False  # See 'Cost and Runtime' in the Markdown cell above!
VERIFY_USING_PRIVATE_WORKFORCE = True # private team leveraged for labelling job

In [5]:
# cell 02
# Make sure the bucket is in the same region as this notebook.
role = sagemaker.get_execution_role()
region = boto3.session.Session().region_name

s3 = boto3.client("s3")
bucket_region = s3.head_bucket(Bucket=BUCKET)["ResponseMetadata"]["HTTPHeaders"][
    "x-amz-bucket-region"
]
assert (
    bucket_region == region
), "You S3 bucket {} and this notebook need to be in the same region.".format(BUCKET)

## Run a Ground Truth labeling job
**This section should take about 20h to complete.**

We will first run a labeling job. This involves several steps: collecting the reviews text we want labeled, specifying the possible label categories, creating instructions, and writing a labeling job specification. In addition, we highly recommend to run a (free) mock job using a private workforce before you submit any job to the public workforce. This notebook will explain how to do that as an optional step. Without using a private workforce, this section until completion of your labeling job should take about 20h. However, this may vary depending on the availability of the public annotation workforce.

## Prepare the data
We will first download IMDB reviews subset of the [IMDB Movie Review Dataset](https://huggingface.co/datasets/pietrolesci/imdb). Later, will compare Ground Truth annotations to these labels. Our dataset will include labels in the following categories:

* Positive
* Negative


If you chose `RUN_FULL_AL_DEMO = False`, then we will choose a subset of 10 reviews text in this dataset. This is a diverse dataset of interesting reviews about movies, and should be fun for the human annotators to work with. You are free to ask the annotators to annotate the sentiments.

We will copy these images to our local `BUCKET`, and will create the corresponding *input manifest*. The input manifest is a formatted list of the S3 locations of the images we want Ground Truth to annotate. We will upload this manifest to our S3 `BUCKET`.

#### Disclosure regarding the Open IMDB Review Dataset V1.0:
Movie Review Dataset V1 is created by Stanford AI Lab. We have not modified the text or the accompanying annotations. You can obtain the text and the annotations [here](http://ai.stanford.edu/~amaas/data/sentiment/).  The following paper describes the learning of word vectors for Sentiment Analysis.

Andrew L. Maas, Raymond E. Daly, Peter T. Pham, Dan Huang, Andrew Y. Ng, and Christopher Potts. (2011). 
*Learning Word Vectors for Sentiment Analysis. The 49th Annual Meeting of the Association for Computational Linguistics (ACL 2011).*([link to PDF](https://aclanthology.org/P11-1015/))

In [24]:
# cell 03
# Download the data if not exists
if not os.path.isfile('tc_dataset.json'):
    !curl -X GET \
     "https://datasets-server.huggingface.co/rows?dataset=pietrolesci%2Fimdb&config=pietrolesci--imdb&split=train&offset=0&limit=100"  >> tc_dataset.json


read_file = pd.DataFrame(columns = ['source'])
text_list = []
# Read and store content of an json file 
with open ('tc_dataset.json', "r") as f:
    # Reading from file
    data = json.loads(f.read())

    # Iterating through the json list
    for i in data['rows']:
        text_list.append(i['row']['text'])
# remove html tags
text_list = [i.replace('<br>', '').replace('</br>', '').replace('<br />','') for i in text_list]

read_file['source'] = text_list


# If running the short version of the demo, reduce each class count 10 times.
if RUN_FULL_AL_DEMO is False:
    text_data = read_file.sample(n=10)
else:
    text_data = read_file

# Create a manifest (jsonline) file
text_data.to_json(r'./input.manifest', orient='records', lines=True)

# Upload the input manifest file to s3
manifest_name = "input/input.manifest"
s3.upload_file(r'./input.manifest', BUCKET, EXP_NAME + "/" + manifest_name)


After running the cell above, you should be able to go to `s3://BUCKET/EXP_NAME/input` in [S3 console](https://console.aws.amazon.com/s3/) and see a 10k reviews. We recommend you inspect the contents of these content! You can download them all to a local machine using the AWS CLI.

## Specify the categories
To run the text classification labeling job, you need to decide on a set of classes the annotators can choose from. 
In our case, this list is `["Positive", "Negative"]`. In your own job you can choose any list of up to 3 classes. We recommend the classes to be as unambiguous and concrete as possible. The categories should be mutually exclusive, with only one correct label per text. 

To work with Ground Truth, this list needs to be converted to a .json file and uploaded to the S3 `BUCKET`.

*Note: The ordering of the labels or classes in the template governs the class indices that you will see downstream in the output manifest (this numbering is zero-indexed). In other words, the class that appears second in the template will correspond to class "1" in the output. At the end of this demonstration, we will train a model and make predictions, and this class ordering is instrumental to interpreting the results.*

In [8]:
# cell 04
# deine the classes
import json
json_body = {"document-version":"2021-05-13",
            "labels":[{"label":"Positive"},
                     {"label":"Negative"}]
            }

with open("class_labels.json", "w") as f:
    json.dump(json_body, f)
    
# upload the json file to s3
s3.upload_file("class_labels.json", BUCKET, EXP_NAME + "/input/class_labels.json")

You should now see `class_labels.json` in `s3://BUCKET/EXP_NAME/input`.

## Create the instruction template
Part or all of your revviews will be annotated by human annotators. It is **essential** to provide good instructions that help the annotators give you the annotations you want. Good instructions are:
1. Concise. We recommend limiting verbal/textual instruction to two sentences, and focusing on clear visuals.
2. Visual. In the case of text classification, we recommend providing one example in each of the classes as part of the instruction.

When used through the AWS Console, Ground Truth helps you create the instructions using a visual wizard. When using the API, you need to create an HTML template for your instructions. Below, we prepare a very simple but effective template and upload it to your S3 bucket.

#### Testing your instructions
It is very easy to create broken instructions. This might cause your labeling job to fail. However, it might also cause your job to complete with meaningless results (when the annotators have no idea what to do, or the instructions are plain wrong). We *highly recommend* that you verify that your task is correct in two ways:
1. The following cell creates and uploads a file called `template.liquid` to S3. It also creates `instructions.html` that you can open in a local browser window. Please do so and inspect the resulting web page; it should correspond to what you want your annotators to see (except the actual image to annotate will not be visible).
2. Run your job in a private workforce, which is a way to run a mock labeling job. We describe how to do it in [Verify your task using a private team [OPTIONAL]](#Verify-your-task-using-a-private-team-[OPTIONAL]).

In [9]:
# cell 05
# a template for text classification
def make_template(test_template=False, save_fname="instructions.template"):
    template = r"""<script src="https://assets.crowd.aws/crowd-html-elements.js"></script>
        <crowd-form>
          <crowd-classifier
            name="crowd-classifier"
            categories="{{ task.input.labels | to_json | escape }}"
            header="TEXT CLASSIFICATION (SINGLE LABEL)"
          >
            <classification-target style="white-space: pre-wrap">
              {{ task.input.taskObject }}
            </classification-target>
            <full-instructions header="Classifier instructions">
              <ol><li><strong>Read</strong> the text carefully.</li>
              <li><strong>Read</strong> the examples to understand more about the options.</li>
              <li><strong>Choose</strong> the appropriate labels that best suit the text.</li></ol>
            </full-instructions>
            <short-instructions>
              <p>Enter description of the labels/sentiments that workers have to choose from</p>
              <p>Positive : If you are positive about things, you are hopeful and confident, and think of the good aspects of a situation rather than the bad ones.". </p>
              <p>Negative : A fact, situation, or experience that is negative is unpleasant, depressing, or harmful.". </p>
                 
              <p><br></p><p><br></p><p>Add examples to help workers understand the label</p>
              <p> Positive : “good”, “great”, “wonderful”, “fantastic”.</p>
              <p> Negative : “bad”, “terrible”, “awful”, “disgusting”.</p>
              <p><br></p><p><br></p><p><br></p><p><br></p><p><br></p>
            </short-instructions>
          </crowd-classifier>
          </crowd-form>"""
    
          
    with open(save_fname, "w") as f:
        f.write(template)
    if test_template is False:
        print(template)


#make_template(test_template=True, save_fname="instructions.html")
make_template(test_template=False, save_fname="template.liquid")
s3.upload_file("template.liquid", BUCKET, EXP_NAME + "/input/template.liquid")
#s3.upload_file("instructions.html", BUCKET, EXP_NAME + "/instructions.html")

<script src="https://assets.crowd.aws/crowd-html-elements.js"></script>
        <crowd-form>
          <crowd-classifier
            name="crowd-classifier"
            categories="{{ task.input.labels | to_json | escape }}"
            header="TEXT CLASSIFICATION (SINGLE LABEL)"
          >
            <classification-target style="white-space: pre-wrap">
              {{ task.input.taskObject }}
            </classification-target>
            <full-instructions header="Classifier instructions">
              <ol><li><strong>Read</strong> the text carefully.</li>
              <li><strong>Read</strong> the examples to understand more about the options.</li>
              <li><strong>Choose</strong> the appropriate labels that best suit the text.</li></ol>
            </full-instructions>
            <short-instructions>
              <p>Enter description of the labels/sentiments that workers have to choose from</p>
              <p>Positive : If you are positive about things, you are

You should now be able to find your template in `s3://BUCKET/EXP_NAME/instructions.template`.

## Assign private team to test your task

Refer to Prerequisites to setup private workforce team. 

Copy private_workteam_arn, from Amazon SageMaker console > Ground Truth > Labeling workforces > Private Teams

The [SageMaker Ground Truth documentation](https://docs.aws.amazon.com/sagemaker/latest/dg/sms-workforce-management-private.html) has more details on the management of private workteams. 

In [11]:
# cell 06
# choose the workforce team
if VERIFY_USING_PRIVATE_WORKFORCE:
    private_workteam_arn = "<< your private workteam ARN here >>"
    WORKTEAM_ARN = private_workteam_arn
else:
    workteam_arn = "arn:aws:sagemaker:{}:394669845002:workteam/public-crowd/default".format(region)
    WORKTEAM_ARN = workteam_arn

print("WORKTEAM_ARN : {}".format(WORKTEAM_ARN))

WORKTEAM_ARN : arn:aws:sagemaker:us-east-1:370501389570:workteam/private-crowd/smgt-immersionday


## Define pre-built lambda functions for use in the labeling job 

Before we submit the request, we need to define the ARNs for four key components of the labeling job: 1) the workteam, 2) the annotation consolidation Lambda function, 3) the pre-labeling task Lambda function, and 4) the machine learning algorithm to perform auto-annotation. These functions are defined by strings with region names and AWS service account numbers, so we will define a mapping below that will enable you to run this notebook in any of our supported regions. 

See the official documentation for the available ARNs:
* [Documentation](https://docs.aws.amazon.com/sagemaker/latest/dg/sms-workforce-management-public.html) for a discussion of the workteam ARN definition. There is only one valid selection if you choose to use the public workfofce; if you elect to use a private workteam, you should check the corresponding ARN for the workteam.
* [Documentation](https://docs.aws.amazon.com/sagemaker/latest/dg/API_HumanTaskConfig.html#SageMaker-Type-HumanTaskConfig-PreHumanTaskLambdaArn) for available pre-human ARNs for other workflows.
* [Documentation](https://docs.aws.amazon.com/sagemaker/latest/dg/API_AnnotationConsolidationConfig.html#SageMaker-Type-AnnotationConsolidationConfig-AnnotationConsolidationLambdaArn) for available annotation consolidation ANRs for other workflows.
* [Documentation](https://docs.aws.amazon.com/sagemaker/latest/dg/API_LabelingJobAlgorithmsConfig.html#SageMaker-Type-LabelingJobAlgorithmsConfig-LabelingJobAlgorithmSpecificationArn) for available auto-labeling ARNs for other workflows.

In [12]:
# cell 07
# Specify ARNs for resources needed to run an text classification job.
ac_arn_map = {
    "us-west-2": "081040173940",
    "us-east-1": "432418664414",
    "us-east-2": "266458841044",
    "eu-west-1": "568282634449",
    "ap-northeast-1": "477331159723",
}
# PreHumanTaskLambdaArn for text classification(single)
prehuman_arn = "arn:aws:lambda:{}:{}:function:PRE-TextMultiClass".format(
    region, ac_arn_map[region]
)

# AnnotationConsolidationConfig for text classification(single)
acs_arn = "arn:aws:lambda:{}:{}:function:ACS-TextMultiClass".format(region, ac_arn_map[region])

# auto-labelling job
labeling_algorithm_specification_arn = "arn:aws:sagemaker:{}:027400017018:labeling-job-algorithm-specification/text-classification".format(
    region
)

## Submit the Ground Truth job request
The API starts a Ground Truth job by submitting a request. The request contains the 
full configuration of the annotation task, and allows you to modify the fine details of
the job that are fixed to default values when you use the AWS Console. The parameters that make up the request are described in more detail in the [SageMaker Ground Truth documentation](https://docs.aws.amazon.com/sagemaker/latest/dg/API_CreateLabelingJob.html).

After you submit the request, you should be able to see the job in your AWS Console, at `Amazon SageMaker > Labeling Jobs`.
You can track the progress of the job there. This job will take several hours to complete. If your job
is larger (say 10,000 review text), the speed and cost benefit of auto-labeling should be larger.

### Verify your task using a private team [OPTIONAL]
If you chose to follow the steps in [Create a private team](#Create-a-private-team-to-test-your-task-[OPTIONAL]), then you can first verify that your task runs as expected. To do this:
1. Set VERIFY_USING_PRIVATE_WORKFORCE to True in the cell below.
2. Run the next two cells. This will define the task and submit it to the private workforce (to you).
3. After a few minutes, you should be able to see your task in your private workforce interface [Create a private team](#Create-a-private-team-to-test-your-task-[OPTIONAL]).
Please verify that the task appears as you want it to appear.
4. If everything is in order, change `VERIFY_USING_PRIVATE_WORKFORCE` to `False` and rerun the cell below to start the real annotation task!

In [13]:
# cell 08
# task definitions
task_description = 'Carefully read and classify this text using the categories provided.'
task_keywords = ['Text classification']
task_title = 'Text Classification (Single Label)'
job_name = "ground-truth-text-classification-" + str(int(time.time()))
USE_AUTO_LABELING = False

# define human task config
human_task_config={
        'PreHumanTaskLambdaArn': prehuman_arn,
        'TaskKeywords': task_keywords,
        'TaskTitle': task_title,
        'TaskDescription': task_description ,
        'NumberOfHumanWorkersPerDataObject': 1,  # number of  workers required to label each text.
        'TaskTimeLimitInSeconds': 300,  # Each text must be labeled within 5 minutes.
        'TaskAvailabilityLifetimeInSeconds': 21600,  # Your worteam has 6 hours to complete all pending tasks.
        'MaxConcurrentTaskCount': 100,   # 100 text sentences will be sent at a time to the workteam.
        'AnnotationConsolidationConfig': {
        'AnnotationConsolidationLambdaArn': acs_arn,
        },
        'UiConfig': {
            'UiTemplateS3Uri': "s3://{}/{}/input/template.liquid".format(BUCKET, EXP_NAME),
        },

    }
    

if not VERIFY_USING_PRIVATE_WORKFORCE:
    human_task_config["PublicWorkforceTaskPrice"] = {
        "AmountInUsd": {
            "Dollars": 0,
            "Cents": 1,
            "TenthFractionsOfACent": 2,
        }
    }
    human_task_config["WorkteamArn"] = workteam_arn
else:
    human_task_config["WorkteamArn"] = private_workteam_arn

ground_truth_request = {
    "InputConfig":{
        'DataSource': {
            'S3DataSource': {
                'ManifestS3Uri': "s3://{}/{}/{}".format(BUCKET, EXP_NAME, manifest_name),
            }
        },
        'DataAttributes': {
            'ContentClassifiers': [
                'FreeOfPersonallyIdentifiableInformation','FreeOfAdultContent',
            ]
        }
    },
    "OutputConfig":{
        'S3OutputPath': "s3://{}/{}/output/".format(BUCKET, EXP_NAME),
    },
    
    "HumanTaskConfig": human_task_config,
    "LabelingJobName": job_name,
    "RoleArn": role,
    "LabelAttributeName": "label",
    "LabelCategoryConfigS3Uri": "s3://{}/{}/input/class_labels.json".format(BUCKET, EXP_NAME),
    "Tags":[
        {
            'Key': 'text',
            'Value': 'text_classification'
        },
    ]


}

if USE_AUTO_LABELING and RUN_FULL_AL_DEMO:
    ground_truth_request["LabelingJobAlgorithmsConfig"] = {
        "LabelingJobAlgorithmSpecificationArn": labeling_algorithm_specification_arn
    }
sagemaker_client = boto3.client("sagemaker")
sagemaker_client.create_labeling_job(**ground_truth_request)

{'LabelingJobArn': 'arn:aws:sagemaker:us-east-1:370501389570:labeling-job/ground-truth-text-classification-1686338403',
 'ResponseMetadata': {'RequestId': '29a05986-717d-4ef2-9357-3de1e32c0b39',
  'HTTPStatusCode': 200,
  'HTTPHeaders': {'x-amzn-requestid': '29a05986-717d-4ef2-9357-3de1e32c0b39',
   'content-type': 'application/x-amz-json-1.1',
   'content-length': '118',
   'date': 'Fri, 09 Jun 2023 19:20:03 GMT'},
  'RetryAttempts': 0}}

In [14]:
# cell 09
# navigate to the private worker portal and do the tasks
workteamName = WORKTEAM_ARN[WORKTEAM_ARN.rfind('/') + 1:]
print("Navigate to the private worker portal and do the tasks. Make sure you've invited yourself to your workteam!")
print('https://' + sagemaker_client.describe_workteam(WorkteamName=workteamName)['Workteam']['SubDomain'])


Navigate to the private worker portal and do the tasks. Make sure you've invited yourself to your workteam!
https://so3zqudq9a.labeling.us-east-1.sagemaker.aws


## Monitor job progress

A Ground Truth job can take a few hours to complete (if your dataset is larger than 1000 reviews, it can take much longer than that!). One way to monitor the job's progress is through AWS Console. In this notebook, we will use Ground Truth output files and Cloud Watch logs in order to monitor the progress. You can re-evaluate the next two cells repeatedly.


You can re-evaluate the next cell repeatedly. It sends a `describe_labelging_job` request which should tell you whether the job is completed or not. If it is, then 'LabelingJobStatus' will be 'Completed'.

In [15]:
# cell 10
# re-evaluate repeatedly. It sends a `describe_labelging_job` request which should tell you whether the job is completed or not. If it is, then 'LabelingJobStatus' will be 'Completed'.
while sagemaker_client.describe_labeling_job(LabelingJobName=job_name)['LabelingJobStatus'] == 'InProgress':
    job_status = sagemaker_client.describe_labeling_job(LabelingJobName=job_name)['LabelingJobStatus']
    print('Labelling job : {}, status : {}'.format(job_name, job_status))
    time.sleep(30)
print('Labelling job : {}, status : {}'.format(job_name, sagemaker_client.describe_labeling_job(LabelingJobName=job_name)['LabelingJobStatus']))

Labelling job : ground-truth-text-classification-1686338403, status : InProgress
Labelling job : ground-truth-text-classification-1686338403, status : InProgress
Labelling job : ground-truth-text-classification-1686338403, status : InProgress
Labelling job : ground-truth-text-classification-1686338403, status : InProgress
Labelling job : ground-truth-text-classification-1686338403, status : InProgress
Labelling job : ground-truth-text-classification-1686338403, status : InProgress
Labelling job : ground-truth-text-classification-1686338403, status : InProgress
Labelling job : ground-truth-text-classification-1686338403, status : InProgress
Labelling job : ground-truth-text-classification-1686338403, status : InProgress
Labelling job : ground-truth-text-classification-1686338403, status : InProgress
Labelling job : ground-truth-text-classification-1686338403, status : InProgress
Labelling job : ground-truth-text-classification-1686338403, status : InProgress
Labelling job : ground-truth

Wait For Workers to Complete Task!

## View Task Results


Once work is completed, SagMaker GroundTruth stores results in your S3 bucket and sends a Cloudwatch event. Your results should be available in the S3 OUTPUT_PATH when all work is completed.

In [16]:
# cell 11
# ouput path
S3_OUTPUT = boto3.client('sagemaker').describe_labeling_job(LabelingJobName=job_name)['OutputConfig']['S3OutputPath'] + job_name
print('S3 OUPUT_PATH : {}'.format(S3_OUTPUT))

# Download human annotation data.
!aws s3 cp {S3_OUTPUT + '/manifests/output/output.manifest'} ./output.manifest #--recursive --quiet

S3 OUPUT_PATH : s3://sagemaker-us-east-1-370501389570/label-text/text-classification/output/ground-truth-text-classification-1686338403
download: s3://sagemaker-us-east-1-370501389570/label-text/text-classification/output/ground-truth-text-classification-1686338403/manifests/output/output.manifest to ./output.manifest


In [17]:
# cell 12
data = []
with open('./output.manifest') as f:
    for line in f:
         data.append(json.loads(line))
pd.DataFrame(data)

source  label  \
0  I rented I AM CURIOUS-YELLOW from my video sto...      1   
1  "I Am Curious: Yellow" is a risible and preten...      0   
2  If only to avoid making this type of film in t...      0   
3  This film was probably inspired by Godard's Ma...      1   
4  Oh, brother...after hearing about this ridicul...      0   

                                      label-metadata  
0  {'class-name': 'Negative', 'job-name': 'labeli...  
1  {'class-name': 'Positive', 'job-name': 'labeli...  
2  {'class-name': 'Positive', 'job-name': 'labeli...  
3  {'class-name': 'Negative', 'job-name': 'labeli...  
4  {'class-name': 'Positive', 'job-name': 'labeli...

## Clean Up [OPTIONAL]

Finally, let's clean up and delete this labeling job

In [18]:
# cell 16
if sagemaker_client.describe_labeling_job(LabelingJobName=job_name)['LabelingJobStatus'] == 'InProgress':
    sagemaker_client.stop_labeling_job(LabelingJobName=job_name) 

## The End!